In [19]:
!pip install hvplot
!pip install jupyter_bokeh
!pip install panel
!pip install bokeh
!pip install holoviews

In [20]:
import pandas as pd
import numpy as np
import panel as pn
pn.extension('tabulator')
import hvplot.pandas

In [21]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

!gdown 'https://drive.google.com/uc?export=download&id=1L42Fjkh8-cPIwswMHK5GtyecYdF-_Xjz'

df = pd.read_csv('owid-covid-data.csv')

Downloading...
From: https://drive.google.com/uc?export=download&id=1L42Fjkh8-cPIwswMHK5GtyecYdF-_Xjz
To: /content/owid-covid-data.csv
100% 93.9M/93.9M [00:00<00:00, 227MB/s]


In [ ]:
# # cache data to improve dashboard performance
# if 'data' not in pn.state.cache.keys():

#     df = pd.read_csv('https://raw.githubusercontent.com/owid/co2-data/master/owid-covid-data.csv')

#     pn.state.cache['data'] = df.copy()

# else:

#     df = pn.state.cache['data']

In [13]:
df

iso_code continent     location        date  total_cases  new_cases  \
0           AFG      Asia  Afghanistan  2020-01-03          NaN        0.0   
1           AFG      Asia  Afghanistan  2020-01-04          NaN        0.0   
2           AFG      Asia  Afghanistan  2020-01-05          NaN        0.0   
3           AFG      Asia  Afghanistan  2020-01-06          NaN        0.0   
4           AFG      Asia  Afghanistan  2020-01-07          NaN        0.0   
...         ...       ...          ...         ...          ...        ...   
358833      ZWE    Africa     Zimbabwe  2023-11-18     265890.0        0.0   
358834      ZWE    Africa     Zimbabwe  2023-11-19     265890.0        0.0   
358835      ZWE    Africa     Zimbabwe  2023-11-20     265890.0        0.0   
358836      ZWE    Africa     Zimbabwe  2023-11-21     265890.0        0.0   
358837      ZWE    Africa     Zimbabwe  2023-11-22     265890.0        0.0   

        new_cases_smoothed  total_deaths  new_deaths  new_deaths_smoothed  \
0                      NaN           NaN         0.0                  NaN   
1                      NaN           NaN         0.0                  NaN   
2                      NaN           NaN         0.0                  NaN   
3                      NaN           NaN         0.0                  NaN   
4                      NaN           NaN         0.0                  NaN   
...                    ...           ...         ...                  ...   
358833                 0.0        5725.0         0.0                  0.0   
358834                 0.0        5725.0         0.0                  0.0   
358835                 0.0        5725.0         0.0                  0.0   
358836                 0.0        5725.0         0.0                  0.0   
358837                 0.0        5725.0         0.0                  0.0   

        ...  male_smokers  handwashing_facilities  hospital_beds_per_thousand  \
0       ...           NaN                  37.746                         0.5   
1       ...           NaN                  37.746                         0.5   
2       ...           NaN                  37.746                         0.5   
3       ...           NaN                  37.746                         0.5   
4       ...           NaN                  37.746                         0.5   
...     ...           ...                     ...                         ...   
358833  ...          30.7                  36.791                         1.7   
358834  ...          30.7                  36.791                         1.7   
358835  ...          30.7                  36.791                         1.7   
358836  ...          30.7                  36.791                         1.7   
358837  ...          30.7                  36.791                         1.7   

        life_expectancy  human_development_index  population  \
0                 64.83                    0.511  41128772.0   
1                 64.83                    0.511  41128772.0   
2                 64.83                    0.511  41128772.0   
3                 64.83                    0.511  41128772.0   
4                 64.83                    0.511  41128772.0   
...                 ...                      ...         ...   
358833            61.49                    0.571  16320539.0   
358834            61.49                    0.571  16320539.0   
358835            61.49                    0.571  16320539.0   
358836            61.49                    0.571  16320539.0   
358837            61.49                    0.571  16320539.0   

        excess_mortality_cumulative_absolute  excess_mortality_cumulative  \
0                                        NaN                          NaN   
1                                        NaN                          NaN   
2                                        NaN                          NaN   
3                                        NaN                          NaN   
4                 

## (0) Some minor data preprocessing

In [14]:
# Fill NAs with 0s and create GDP per capita column
df = df.dropna(subset=['continent'])
print(df['continent'].unique())

['Asia' 'Europe' 'Africa' 'Oceania' 'North America' 'South America']


In [ ]:
# Define Panel widgets
year_slider = pn.widgets.IntSlider(name='date', start=2020, end=2023)
year_slider

IntSlider(end=2023, name='date', start=2020, value=2020)

In [ ]:
# Radio buttons for CO2 measures
yaxis_co2 = pn.widgets.RadioButtonGroup(
    name='Y axis',
    options=['co2', 'co2_per_capita',],
    button_type='success'
)

In [24]:
# %%
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

!gdown 'https://drive.google.com/uc?export=download&id=1L42Fjkh8-cPIwswMHK5GtyecYdF-_Xjz'

df = pd.read_csv('owid-covid-data.csv')

# Convert 'date' column to datetime
df['date'] = pd.to_datetime(df['date'])


df
# %% [markdown]
# ## (0) Some minor data preprocessing
# %%
# Fill NAs with 0s and create GDP per capita column
df = df.dropna(subset=['continent'])
print(df['continent'].unique())
# %%
import pandas as pd
import matplotlib.pyplot as plt
from ipywidgets import interact, widgets

# Ensure 'date' column is in datetime format
# df.loc[:, 'date'] = pd.to_datetime(df['date'])

# Extract unique values for continents and countries
continents = df['continent'].dropna().unique()  # Handle potential NaN values
countries = df['location'].unique()
years = [2020, 2021, 2022, 2023]  # Limit years for simplicity

# Create a function to filter countries based on the selected continent
def get_countries_by_continent(continent):
    if continent:
        return df[df['continent'] == continent]['location'].unique()
    else:
        return []

# Define the plotting function
def plot_data(continent, country, year):
    # Filter the data based on user selection
    filtered_data = df[(df['continent'] == continent) &
                       (df['location'] == country) &
                       (df['date'].dt.year == year)]

    # Check if there's data to plot
    if filtered_data.empty:
        print(f"No data available for {country} in {year}.")
        return

    # Set up the figure
    fig, axes = plt.subplots(2, 2, figsize=(16, 12))

    # Plot 1: Total Cases Over Time
    axes[0, 0].plot(filtered_data['date'], filtered_data['total_cases'], label='Total Cases', color='blue', linewidth=2)
    axes[0, 0].set_title(f'Total Cases in {country} ({year})', fontsize=14)
    axes[0, 0].set_xlabel('Date', fontsize=12)
    axes[0, 0].set_ylabel('Total Cases', fontsize=12)
    axes[0, 0].grid(True, linestyle='--', alpha=0.6)

    # Plot 2: Total Deaths Over Time
    axes[0, 1].plot(filtered_data['date'], filtered_data['total_deaths'], label='Total Deaths', color='red', linewidth=2)
    axes[0, 1].set_title(f'Total Deaths in {country} ({year})', fontsize=14)
    axes[0, 1].set_xlabel('Date', fontsize=12)
    axes[0, 1].set_ylabel('Total Deaths', fontsize=12)
    axes[0, 1].grid(True, linestyle='--', alpha=0.6)

    # Plot 3: Total Vaccinations Over Time
    axes[1, 0].plot(filtered_data['date'], filtered_data['total_vaccinations'], label='Total Vaccinations', color='green', linewidth=2)
    axes[1, 0].set_title(f'Total Vaccinations in {country} ({year})', fontsize=14)
    axes[1, 0].set_xlabel('Date', fontsize=12)
    axes[1, 0].set_ylabel('Total Vaccinations', fontsize=12)
    axes[1, 0].grid(True, linestyle='--', alpha=0.6)

    # Plot 4: New Cases Over Time
    axes[1, 1].plot(filtered_data['date'], filtered_data['new_cases'], label='New Cases', color='orange', linewidth=2)
    axes[1, 1].set_title(f'New Cases in {country} ({year})', fontsize=14)
    axes[1, 1].set_xlabel('Date', fontsize=12)
    axes[1, 1].set_ylabel('New Cases', fontsize=12)
    axes[1, 1].grid(True, linestyle='--', alpha=0.6)

    # Add a main title
    plt.suptitle('Covid19 Dashboard', fontsize=20, fontweight='bold', y=1.02)

    # Adjust layout
    for ax in axes.flat:
        ax.legend(fontsize=10)
        ax.tick_params(axis='x', rotation=45)
    plt.tight_layout()
    plt.show()

# Create interactive widgets for continent and year
continent_widget = widgets.Dropdown(options=continents, description='Continent:')
year_widget = widgets.IntSlider(
    min=2020,
    max=2023,
    step=1,
    value=2020,
    description='Year:',
    continuous_update=False
)

# Create the country widget with initial options based on the selected continent
country_widget = widgets.Dropdown(description='Country:')

# Update the countries dropdown when a continent is selected
def update_country_options(continent):
    country_widget.options = get_countries_by_continent(continent)

# Link the continent widget to the update function
continent_widget.observe(lambda change: update_country_options(change.new), names='value')

# Set initial country options
update_country_options(continent_widget.value)

# Create the interactive plot
interact(
    plot_data,
    continent=continent_widget,
    country=country_widget,
    year=year_widget
);

Downloading...
From: https://drive.google.com/uc?export=download&id=1L42Fjkh8-cPIwswMHK5GtyecYdF-_Xjz
To: /content/owid-covid-data.csv
100% 93.9M/93.9M [00:00<00:00, 224MB/s]
['Asia' 'Europe' 'Africa' 'Oceania' 'North America' 'South America']


interactive(children=(Dropdown(description='Continent:', options=('Asia', 'Europe', 'Africa', 'Oceania', 'Nort…